In [1]:
###########LIBRARY CELL###########
# pip install watermark
%load_ext watermark
%watermark -v -m -p numpy,scipy,pandas,matplotlib,sklearn -g 
#,statsmodels

CPython 3.6.8
IPython 7.7.0

numpy 1.17.0
scipy 1.3.1
pandas 0.25.0
matplotlib 3.1.1
sklearn 0.21.3

compiler   : GCC 8.0.1 20180414 (experimental) [trunk revision 259383
system     : Linux
release    : 4.9.93-boot2docker
machine    : x86_64
processor  : x86_64
CPU cores  : 2
interpreter: 64bit
Git hash   : f325bf5e3ff7d8396fe133b30c3bbb2b5f7ef8a0


In [2]:
###########LIBRARY CELL###########
from __future__ import division, print_function
import warnings
warnings.filterwarnings('ignore')
import os
import numpy as np
import pandas as pd
import math
import datetime
import re
import sys

In [3]:
###########LIBRARY CELL###########
COMPARATOR_AUTHOR = "Anton Tushev" 
COMPARATOR_VERSION = "v.33"
PATH_TO_DATA = '/notebooks/pinda/data'
PATH_TO_STRUCG = '/notebooks/pinda/data/alcanc16_07_2019'
#PATH_TO_STRUCG = '/notebooks/pinda/data/test'
PATH_TO_REPORTS = '/notebooks/pinda/reports'
FILE_NAME_DATA1 = 'TX01_TX01_PS.csv'
#FILE_NAME_DATA1 = 'test.csv'
SD_RACK_NAMES = ['tx01']
FILE_NAME_TEMP0 = '@data_a1_progress_bkup.csv'
FILE_NAME_TEMP1 = '@data_s1_progress_bkup.csv'
FILE_NAME_TEMP2 = '@data_ls1_progress_bkup.csv'
FILE_NAME_TEMP3 = '@data_lm_progress_bkup.csv'
#FILE_NAME_DATA1 = 'test.csv'
IGNORE_CHART = ['@SIMD']
SKIP_CHART_NFND = False
SKIP_BLOCK_NEXST = False
SKIP_SIGNAL_NFND = False
SKIP_EQUAL = True
SKIP_TYPE_STR = False

COMPARATOR_README = "===================================================================================\
\r\nAdvanced comparator SimadynD <=> TDC software version: %s \r\nAuthor: %s \
\r\nComparison result made from %s StrucG folder \
\r\nTDC data file is '%s' \
\r\nList of SimadynD subfolders for parsing is %s \
\r\nList of ignored charts is %s \
\r\n===================================================================================\
"%(COMPARATOR_VERSION,COMPARATOR_AUTHOR,PATH_TO_STRUCG,FILE_NAME_DATA1,SD_RACK_NAMES,IGNORE_CHART)
print(COMPARATOR_README)

Advanced comparator SimadynD <=> TDC software version: v.28 
Author: Anton Tushev 
Comparison result made from /notebooks/pinda/data/alcanc16_07_2019 StrucG folder 
TDC data file is 'TX01_TX01_PS.csv' 
List of SimadynD subfolders for parsing is ['tx01'] 
List of ignored charts is ['@SIMD'] 


In [135]:
#data_a1 = pd.read_csv(os.path.join(PATH_TO_DATA,FILE_NAME_DATA1),keep_default_na=False,na_values=[''], encoding="cp1251",sep=';',header=0)
#data_a1

In [5]:
###########EXECUTION CELL###########
#Load TDC data
data_a1 = pd.read_csv(os.path.join(PATH_TO_DATA,FILE_NAME_DATA1),keep_default_na=False,na_values=[''], encoding="cp1251",sep=';',header=0)
data_a1 = data_a1[data_a1.columns[[0,1,2,3,5,7,14,15]]]
data_a1.columns = ['rack_cpu','chart','block','signal','value','link','type','out']
data_a1 = pd.concat([data_a1, data_a1['rack_cpu'].str.split("\\",expand = True)[[0,1]]], axis=1) 
data_a1.columns = ['rack_cpu','chart','block','signal','value','link','type','out','rack','cpu']
data_a1["out"]= data_a1["out"].replace(("IN","OUT"),(0,1)).astype('bool') 
data_a1 = data_a1[~data_a1['chart'].isin(IGNORE_CHART)]
data_a1["block"] = data_a1["block"].astype(str)
data_a1["chartblock"] = data_a1["chart"].str.upper()+"/"+data_a1["block"].str.upper()
data_a1["chart_block_signal"] = data_a1["chart"].str.upper()+"/"+data_a1["block"].str.upper()+"."+data_a1["signal"].str.upper()
data_a1['value_linked'] = np.where(data_a1['link'].isnull(), data_a1['value'],data_a1['link'].str.strip('"').str.split('"',n=1,expand=True)[0] )
#print("Data types ",data_a1['type'].unique())
#print("Charts ",data_a1['chart'].unique())
#print(data_a1[(~data_a1['link'].isnull())&(data_a1['out']==True)])
data_a1.head()

rack_cpu   chart block signal    value  \
0  TX01\D01P01\  DIN2_1     1      I      NaN   
1  TX01\D01P01\  DIN2_1     1      Q  16#0000   
2  TX01\D01P01\  DIN2_1    10    X01  16#0000   
3  TX01\D01P01\  DIN2_1    10    X02      NaN   
4  TX01\D01P01\  DIN2_1    10    X03      NaN   

                                link  type    out  rack     cpu chartblock  \
0                       !MCDMB1.0001  WORD  False  TX01  D01P01   DIN2_1/1   
1  DIN2_1\MCB101.X1"DIN2_1\MCB101.X1  WORD   True  TX01  D01P01   DIN2_1/1   
2                                NaN  WORD  False  TX01  D01P01  DIN2_1/10   
3                       !HYDMB1.0001  WORD  False  TX01  D01P01  DIN2_1/10   
4                       !HYDMB1.0002  WORD  False  TX01  D01P01  DIN2_1/10   

  chart_block_signal      value_linked  
0         DIN2_1/1.I      !MCDMB1.0001  
1         DIN2_1/1.Q  DIN2_1\MCB101.X1  
2      DIN2_1/10.X01           16#0000  
3      DIN2_1/10.X02      !HYDMB1.0001  
4      DIN2_1/10.X03      !HYDMB1.0002

In [4]:
###########LIBRARY CELL###########
#Generate Simadyn chart structure
def sd_get_chart_list(PATH_TO_STRUCG=PATH_TO_STRUCG,SD_RACK_NAMES=SD_RACK_NAMES):
    #filter chart files
    n = re.compile("^(((?!old).)*).((cfp)|(ufp))$")
    file_list=[] 
    file_list = {rack_name:[item for item in os.listdir(os.path.join(PATH_TO_STRUCG,rack_name)) \
        # chart file names filter conditions
        if os.path.isfile(os.path.join(PATH_TO_STRUCG,rack_name, item)) and (n.search(item)) and len(item)<11 \
        ] for rack_name in SD_RACK_NAMES}
    file_list_filtered = dict(file_list)
    for i in file_list:
        for k in file_list[i]:
            chart_name = k.split('.')[0]
            if "%s.cfp"%chart_name in file_list[i]:
                try:
                    file_list_filtered[i].remove("%s.ufp"%chart_name)
                except ValueError:
                    pass  # do nothing
    out_dict = dict()
    for i in file_list_filtered:
        out_dict[i] = dict()
        for k in file_list_filtered[i]:
            out_dict[i][k.split('.')[0]]=os.path.join(PATH_TO_STRUCG,i,k)
    if out_dict:
        return out_dict
    else:
        return -1
    
#Generate Simadyn cpu mapping structure
def sd_get_cpu_charts_list(PATH_TO_STRUCG=PATH_TO_STRUCG,SD_RACK_NAMES=SD_RACK_NAMES):
    #filter chart files
    n = re.compile("^((\d+).*)\.(mpn)$")
    file_list=[] 
    file_list=[] 
    file_list = {rack_name:[item for item in os.listdir(os.path.join(PATH_TO_STRUCG,rack_name)) \
        # chart file names filter conditions
        if os.path.isfile(os.path.join(PATH_TO_STRUCG,rack_name, item)) and (n.search(item)) and len(item)<11 \
        ] for rack_name in SD_RACK_NAMES}
    out_dict = dict()
    for i in file_list:
        out_dict[i] = dict()
        for k in file_list[i]:
            out_dict[i][k.split('.')[0]]=os.path.join(PATH_TO_STRUCG,i,k)
    if out_dict:
        return out_dict
    else:
        return -1

#for debug
##output => #sd_chart_list {"tx03":{'chrt_name':file_addrs}}
    




In [5]:
###########EXECUTION CELL###########
sd_chart_list = sd_get_chart_list() 
sd_cpu_charts_list = sd_get_cpu_charts_list() 

In [300]:
###########TEST CELL, IGNORE###########
#n = re.search("^(((?!old).)*).((cfp)|(ofp))$", 'pray1___20131208.cfp')
test_txt = []
test_txt.append(" 129	X01 V2 < 0H0,!E2C113.0011&")
test_txt.append(" 325	I1  B1 < VIHW09.Q15&")
test_txt.append("1397	CCI N2 < DMVI04.Y ")
test_txt.append("1447	I3  B1 < VII250.Q9  ,'ENNROLRD' \"SECTION NOT READY FOR ROLLING\"")
test_txt.append("1229	AD  NK = *ADRCO1,'DO5I2X6A'")
test_txt.append(" 100	IS  V2 < $VST1LS\"Limit switches stand movements 1\"")
test_txt.append('  81	IS  V2 < $VISW17')
test_txt.append(" 163	Q1  B1 > ,'Man__CPS'            \"MAINTENANCE COIL PREP STATION\"")
test_txt.append(' 115	I1  B1 < VIHW17.Q2&')
test_txt.append(' 519	X1  N2 < @TYP=V2,0HFFFF')
test_txt.append(" 150	Y   N2 > @TYP=O2,'RP_ALL'&")
test_txt.append(' 520	X2  N2 < @TYP=V2,LB2.QS&')
test_txt.append(' 527	QS  V2 > $VGAU02                "Diagnose 2nd direction"')
test_txt.append(' 528	Q   B1 > ')
test_txt.append("  31	AD  NK = D02_I1.X8C")
test_txt.append("  32	DM  B1 - 1")
test_txt.append("  22	AR  NS - 'B1G1X1'")
test_txt.append("  21	CTS CR - D0300A")
test_txt.append("1151	T1  NS - '@F@85@ EN QFC Coil P. Shear Tab. Air Float'")
test_txt.append("1199	X1  N2 < 0%")
test_txt.append("1200	X2  N2 < SEND07.QS")
test_txt.append("1201	I   B1 < EN_MES.Q,'EN_MES'&")
test_txt.append(" 566	LZU NF < #10000[ms],'RunTime '  \"Run time monitoring\"")
test_txt.append("1207	X2  N2 < 18.298%                \"18,3 representa 3000 kg\"")
test_txt.append("1283	X2  NF < #0")
test_txt.append("1304	X2  NF < #26,'GRAUS'")
test_txt.append(" 905	X2  NF < #100.0000000E3")
test_txt.append("1074	Y   NF > @TYP=TF,$PTTI_A,'PTTI_AUT'&")
test_txt.append("1073	X   NF < @TYP=TF,10[S]")
test_txt.append("2983	X2  NF < #530.0000000E-3,'m'")
test_txt.append(" 439	FBU NF < #500[ms],'Feedback'    \"Feedback monitoring\"")
test_txt.append(" 494	I   B1 < STG641.Q")
test_txt.append(" 495	Y   N2 > @TYP=V2")
test_txt.append("  17	X1  NF < $XIHW05,SCAL=1[m]")
test_txt.append(" 374	T   TF <  3           [s]")
test_txt.append(" 169	T   TF <            2[s ]")
test_txt.append("2946	OR  V2 < 0B00000000 00000000")
test_txt.append(" 108	X05 NF < #2500.0[V/(m/s)],'ky'  \"Scaling factor for control output\"&")
test_txt.append("2756	CRT TR = !EXM504")
test_txt.append(" 337	Q1  B1 >")
test_txt.append("1407	T   TF < #2.5 [s]")
test_txt.append("  87	Q3  B1 > $E_STOP PN,'E_STOP'&")
test_txt.append(" 267	X   NF < #1E+6")
test_txt2 = " 439	FBU NF < #500[ms],'Feedback'    \"Feedback monitoring\""


#m = re.compile(r"^\s*\d+\s+(\w+)\s+(\w+)\s+([<>])\s+(@TYP=(..),)?([^@\"',&]+)([,\"'&]|$)", )
m = re.compile(r"""
        ^\s*\d+\s+ #string number
        (\w+)\s+   #signal name 
        (\w+)\s+   #signal type 
        ([<>=-])\s*  #signal delimiter 
        (@TYP=(..),?)? #singal type
        (   #value
        ([a-zA-Z0-9_.]+)|  #can be connection to other block
        ([$%!\[\]/()a-zA-Z0-9_.#\-\+]+)|  #can be value
        ([$a-zA-Z0-9_]+\s*[$a-zA-Z0-9_]*)|  #can be virtual connection
        ([#0-9.]+\s*\[.*\])|  #can be time with spaces
        ([0-9B]+\s+[0-9]+)|  #can be hex in bit representation
        ('.*')| #can be text
        (\*[a-zA-Z0-9_.]+)  #can hardware connection: *ADRCO1
        )? #end of value
        ([\s]*,)? #divider
        (\![a-zA-Z0-9_\.]+)?
        ([\s]*,)?
        ('.*')? #link comment
        (,.*)? #some comment
        (\s*".*")? #signal comment
        (&)? #check next string
        (\s)*
        ($) #end of string
        
        """, re.X)
k = re.compile(r"^\s*\d+\s+(\w+)\s+(\w+)\s+([<>=-])")

for a in test_txt:
    n = m.search(a)
    print(a)
    #print(n.group(1),n.group(2),n.group(3),n.group(5),n.group(6),n.group(13))
    #print(n)
    print(n.group(6),n.group(15))
    #print(n)
    
#n = m.search(test_txt2)
#print("OUT:",n.group(1),n.group(2),n.group(3),n.group(6),n.group(13))

#for a in test_txt:
#    n = k.search(a)
#    print(n)

#for a in test_txt:
#    n = k.search(a)
#    print(n)

 129	X01 V2 < 0H0,!E2C113.0011&
0H0 !E2C113.0011
 325	I1  B1 < VIHW09.Q15&
VIHW09.Q15 None
1397	CCI N2 < DMVI04.Y 
DMVI04.Y None
1447	I3  B1 < VII250.Q9  ,'ENNROLRD' "SECTION NOT READY FOR ROLLING"
VII250.Q9 None
1229	AD  NK = *ADRCO1,'DO5I2X6A'
*ADRCO1 None
 100	IS  V2 < $VST1LS"Limit switches stand movements 1"
$VST1LS None
  81	IS  V2 < $VISW17
$VISW17 None
 163	Q1  B1 > ,'Man__CPS'            "MAINTENANCE COIL PREP STATION"
None None
 115	I1  B1 < VIHW17.Q2&
VIHW17.Q2 None
 519	X1  N2 < @TYP=V2,0HFFFF
0HFFFF None
 150	Y   N2 > @TYP=O2,'RP_ALL'&
'RP_ALL' None
 520	X2  N2 < @TYP=V2,LB2.QS&
LB2.QS None
 527	QS  V2 > $VGAU02                "Diagnose 2nd direction"
$VGAU02 None
 528	Q   B1 > 
None None
  31	AD  NK = D02_I1.X8C
D02_I1.X8C None
  32	DM  B1 - 1
1 None
  22	AR  NS - 'B1G1X1'
'B1G1X1' None
  21	CTS CR - D0300A
D0300A None
1151	T1  NS - '@F@85@ EN QFC Coil P. Shear Tab. Air Float'
'@F@85@ EN QFC Coil P. Shear Tab. Air Float' None
1199	X1  N2 < 0%
0% None
1200	X2  N2 < SEND07.

In [298]:
test_txt=(" 129	X01 V2 < 0H0,!E2C113.0011&")
n = re.compile(r"""
        ^\s*\d+\s+ #string number
        (\w+)\s+   #signal name 
        (\w+)\s+   #signal type 
        ([<>=-])\s*  #signal delimiter 
        (@TYP=(..),?)? #singal type
        (   #value
        ([a-zA-Z0-9_.]+)|  #can be connection to other block
        ([$%!\[\]/()a-zA-Z0-9_.#\-\+]+)|  #can be value
        ([$a-zA-Z0-9_]+\s*[$a-zA-Z0-9_]*)|  #can be virtual connection
        ([#0-9.]+\s*\[.*\])|  #can be time with spaces
        ([0-9B]+\s+[0-9]+)|  #can be hex in bit representation
        ('.*')| #can be text
        (\*[a-zA-Z0-9_.]+)  #can hardware connection: *ADRCO1
        )? #end of value
        ([\s]*,)? #divider
        (\![a-zA-Z0-9_\.]+)?
        (&)? #check next string
        (\s)*
        ($) #end of string
        
        """, re.X)
a=n.search(test_txt)
print(a.group(15))

!E2C113.0011


In [142]:
###########TEST CELL, IGNORE###########
#test_txt="   &	V4.2.6 FP-COP CHK 22.02.;9 07:54  (MP-TX04.PN-D05_P2 13.09.;6 05:02)"
#test_txt = "   1 PN-D01_P1"
#test_txt = "1832	*"
#test_txt = ""
#test_txt = "  89 Connector list of the function packets"
#test_txt = "1816	FP-@SEND1,COM"
#test_txt = "1679	   $VINS02 T4 < PN     PN-D01_P1"
test_txt = " 830	   $DIADE  T4 < PN     PN-D01_P1"
test_txt = "ENMESS.Q1231"

#cp = re.compile(r'^\s+\d+\s+([a-zA-Z0-9_-]+)$')
#cp = re.compile(r'^\s+\d+\s+Connector list of the function packets')
#cp = re.compile(r'^\s*\d+\s+\*')
#cp = re.compile(r'^\s*\d+\s+FP-([a-zA-Z0-9_\-@]+)')
#cp = re.compile(r'^\s*\d+\s+(\$[a-zA-Z0-9_\-@]+)\s+([\w]+)\s((<)|(>))\s([\w]+)\s+([a-zA-Z0-9_-]+)$')
cp = re.compile(r'^[a-zA-Z0-9_\-@]+\.[a-zA-Z0-9_\-@]+$')
cp_s = cp.search(test_txt)
print(cp_s)
#print(cp_s.group(1),cp_s.group(3),cp_s.group(7))

<_sre.SRE_Match object; span=(0, 12), match='ENMESS.Q1231'>


In [123]:
###########TEST CELL, IGNORE###########
test_txt = []
test_txt.append("   &		(SEND01.I9)")
test_txt.append('   &		(KA1014.I2,KA1015.I2)')
k = re.compile(r"^\s*&+\s+\((.*)\)\s*$")
for a in test_txt:
    n = k.search(a)
    print(n.group(1))
    #print(n)

SEND01.I9
KA1014.I2,KA1015.I2


In [10]:
###########LIBRARY CELL###########
#########################SimadynD row data generating library#################
NAME,TYPE_BASE,INOUT,TYPE_CONV,VALUE,CPU,CPU_SOURCE,CPU_LINK,CHART,BLOCK, LINKS  = 0,1,2,3,4,5,6,7,8,9,10

#open chart for reading
def sd_open_chart(chart_addr):
    try:
        with open(chart_addr) as f:
            lines = [line.rstrip('\n') for line in f]
    except EnvironmentError: # parent of IOError, OSError *and* WindowsError where available
        #print('ERROR File not exists!')
        return -1
    return lines

#generate chart mapping: line {block name:[block line begin, block line end]}
def sd_get_chart_map(inp_line):
    b = re.compile(r"^\s*\d+ ?([a-zA-Z0-9_]+) +: [a-zA-Z0-9_.@]+\s*,\s*POS=")
    el = re.compile(r'^ *\d+\s+[+]')
    #cp = re.compile(r'\(([a-zA-Z0-9_-]+).([a-zA-Z0-9_-]+)\s+\S+\s+\S+\)') #not used, because not all charts consist
    block_list = []
    mark_bloc = False
    #mark_cpu = False
    out_dict = dict()
    line_counter = 0
    for k in inp_line:
        #Find rack name and cpu name, e.g. MP-TX04 PN-D05_P2
        #if not mark_cpu:
        #    cp_s = cp.search(k)
        #    if cp_s :
        #        rack,cpu = cp_s.group(1),cp_s.group(2)
        #        mark_cpu = True
        b_s = b.search(k)
        if b_s :
            mark_bloc = True
            curr_block_name = b_s.group(1)
            block_list.append(curr_block_name)
            mark_bloc_line_beg = line_counter
        elif el.search(k):
            if mark_bloc:
                mark_bloc = False
                out_dict[curr_block_name] = [mark_bloc_line_beg,line_counter]
        line_counter = line_counter+1        
    #print(len(block_list))
    if(out_dict):
        return out_dict
    else:
        return -1

#check if line is signal or link
def sd_check_line_signal(line):
    sf = re.compile(r"^\s*\d+\s+(\w+)\s+(\w+)\s+([<>=-])")
    sa = re.compile(r"^\s*&+\s+(\(.*\))\s*$")
    if sf.search(line):
        out = 1 #signal
    elif sa.search(line):
        out = 2 #link
    else:
        out = 0 #nothing
    return out

#extract data from signal line
def sd_get_line_data(line): 
    m = re.compile(r"""
        ^\s*\d+\s+ #string number
        (\w+)\s+   #signal name 
        (\w+)\s+   #signal type 
        ([<>=-])\s*  #signal delimiter 
        (@TYP=(..),?)? #singal type
        (   #value
        ([a-zA-Z0-9_.]+)|  #can be connection to other block
        ([$%!\[\]/()a-zA-Z0-9\s_.*#\-\+]+)|  #can be value
        ([$a-zA-Z0-9_]+\s*[$a-zA-Z0-9_]*)|  #can be virtual connection
        ([#0-9.]+\s*\[.*\])|  #can be time with spaces
        ([0-9B]+\s+[0-9]+)|  #can be hex in bit representation
        ('.*')| #can be text
        (\*[a-zA-Z0-9_.]+)  #can hardware connection: *ADRCO1
        )? #end of value
        ([\s]*,)? #divider
        (\![a-zA-Z0-9_\.]+)?
        ([\s]*,)?
        ('.*')? #link comment
        (,.*)? #some comment
        (\s*".*")? #signal comment
        (&)? #check next string
        (\s)*
        ($) #end of string
        """, re.X)
    #print(line)
    n = m.search(line)
    try:
        #Check if value is XXXX but behind is telegram connection like !XXX.YY
        if n.group(15):
            check_val = n.group(15)
        else:
            check_val = n.group(6)
        out = list([n.group(1),n.group(2),n.group(3),n.group(5),check_val])
    except:
        print(line)
        raise
        
    #     #name      type       dir        type_conv  value 
    #list([n.group(1),n.group(2),n.group(3),n.group(5),n.group(6)])
    return out

#exstract link from like
def sd_get_line_link(line): 
    m = re.compile(r"^\s*&+\s+\((.*)\)\s*$")
    n = m.search(line)     
    return n.group(1)  

#get block data: signals, values, links, data types...
def sd_get_block_data(lines,chart,block,data_link_map_df):

    mark_signal_row_name = None
    mark_signal_row_data = list([[],[]]) #[[signal data],[links]]
    mark_block_row_data = []
    count = 0;
    #get CPU name
    cpu = sd_get_chart_cpu(data_link_map_df,chart)
    #If no cpu found, it means chart is not used in SD software:
    if cpu == -1:
        return -1
    for l in lines:
        line_check_result = sd_check_line_signal(l)
        if line_check_result:
            if line_check_result==1:  
                #if found a signal line
                count = count+1
                #add previous signal to preparation table
                if mark_signal_row_name:
                    #print("Old name:",mark_signal_row_name)
                    mark_block_row_data.append(mark_signal_row_data)
                    mark_signal_row_data = list([[],[]]) #reset buffer table
                #NAME,TYPE_BASE,INOUT,TYPE_CONV,VALUE
                mark_signal_row_data[0] = sd_get_line_data(l)
                mark_signal_row_data[0].append(cpu)
                #If value is $LINK here is a logic:
                #Copy value $LINK to link column
                if re.search(r'^\$',str(mark_signal_row_data[0][VALUE])) and mark_signal_row_data[0][INOUT]=="<":
                    link = mark_signal_row_data[0][VALUE].split()[0] #CONVERT '$LINK PN' => '$LINK'
                    mark_signal_row_data[1].append(link)
                    #get CPU_SOURCE
                    cpu_source = sd_get_block_link_source_cpu(data_link_map_df,link,chart)
                    mark_signal_row_data[0].append(cpu_source)
                    #get CPU_LINK   (means CPU_SOURCE_LINK)
                    mark_signal_row_data[0].append(cpu_source+"_"+link)
                else:
                    #get CPU_SOURCE
                    mark_signal_row_data[0].append(cpu)
                    #get CPU_LINK   (means CPU_SOURCE_LINK)
                    mark_signal_row_data[0].append(None)
                    
                mark_signal_row_name = mark_signal_row_data[0][NAME]
                #get CHART,BLOCK
                mark_signal_row_data[0].append(chart)
                mark_signal_row_data[0].append(block)
            elif line_check_result==2:
                #if found a link line: (SOMETHING,SOMETHING2)
                mark_signal_row_data[1].extend(sd_get_line_link(l).split(','))
            #print(mark_signal_row_data)            
        else:
            pass #skip string
    #Add last signal to preparation storage
    mark_block_row_data.append(mark_signal_row_data)
    return mark_block_row_data

#convert list to pandas data frame
def sd_conv_block_data_to_df(block_data):
    #list element of row signal data:[[NAME,TYPE_BASE,INOUT,TYPE_CONV,VALUE],[links]]
    block_df = pd.DataFrame([[j for j in k[0]]+[k[1]] for k in block_data])
    return block_df
#convert list to better representation
def sd_conv_block_data_to_list(block_data):
    #list element of row signal data:[[NAME,TYPE_BASE,INOUT,TYPE_CONV,VALUE,CPU,CPU_SOURCE,CPU_LINK,CHART,BLOCK],[links]]
    block_data_list = [[j for j in k[0]]+[k[1]] for k in block_data]
    return block_data_list


#create df row with link source structure: chart_block_signal,cpu_link
def sd_get_source_link(block_data_list):
    #block_data_list: (NAME,TYPE_BASE,INOUT,TYPE_CONV,VALUE,CPU,CPU_SOURCE,CPU_LINK,CHART,BLOCK ),LINKS
    m = re.compile(r"^\$\w+")
    out_df = []
    for j in block_data_list:
        if j[INOUT]==">":
            if(j[INOUT]):
                
                val = str(j[VALUE])
                n = m.search(val) 
                if n:
                    #chart\block.signal,cpu_link
                    chart_block_signal = j[CHART].upper()+'\\'+j[BLOCK].upper()+'.'+j[NAME].upper()
                    cpu_link = j[CPU]+'_'+val.split()[0] #convert '$LINK PN' => '$LINK'
                    #print(chart_block_signal,"=>",cpu_link)
                    out_df.append([chart_block_signal,cpu_link])
            #look for source link in link array
            for k in j[LINKS]:
                if(k):
                    n = m.search(str(k)) 
                    if n:
                        #chart\block.signal,cpu_link
                        chart_block_signal = j[CHART].upper()+'\\'+j[BLOCK].upper()+'.'+j[NAME].upper()
                        cpu_link = j[CPU]+'_'+str(k).split()[0] #convert '$LINK PN' => '$LINK'
                        #print(chart_block_signal,"=>",cpu_link)
                        out_df.append([chart_block_signal,cpu_link])
    return out_df

#generate data of all charts and generate data of link sources
def sd_build_data_s1(sd_chart_list,data_link_map_df):
    
    data_list = []
    data_link_source_list = []
    for i in sd_chart_list:
        for (k,v) in sd_chart_list[i].items(): 
            chart = k.upper()
            chart_lines = sd_open_chart(v)
            chart_mapping = sd_get_chart_map(chart_lines)
            if chart_mapping==-1:
                print("Parsing '%s' chart with 0 functions"%(chart))
                continue
            else:
                print("Parsing '%s' chart with %s functions"%(chart,len(chart_mapping)))
            
            for block_map in chart_mapping:
                #generating array 'signal','type_base','inout','type_conv','value','link','chart','block','cpu'
                block_lines = chart_lines[chart_mapping[block_map][0]:chart_mapping[block_map][1]]
                #get block data: NAME,TYPE_BASE,INOUT,TYPE_CONV,VALUE,CPU,CPU_SOURCE,CPU_LINK,CHART,BLOCK
                block_data = sd_get_block_data(block_lines,chart,block_map,data_link_map_df)
                if block_data == -1:
                    print("Parsing cancelled: '%s' chart is not used in SimadynD program"%(chart))
                    break
                #print("before ",block_data)
                #print("-- ")
                block_data_list = sd_conv_block_data_to_list(block_data)
                #print("after ",block_data_list)
                #print("-- ")
                #Add block data to accumulation list
                data_list.extend(block_data_list)
                #create link source array
                block_link_source_list = sd_get_source_link(block_data_list)
                if len(block_link_source_list)!=0:
                    #print(block_link_source_list)
                    data_link_source_list.extend(block_link_source_list) 
    #Convert to DataFrame for easy work
    data_link_source_df = pd.DataFrame(data_link_source_list, columns=['chart_block_signal','cpu_link'])
    data_df = pd.DataFrame(data_list, columns=['signal','type_base','inout','type_conv','value','cpu',\
                                                         'cpu_source','cpu_link','chart','block','link'])
    return data_df,data_link_source_df

#parsing mapping file
#generate cpu,link db by cpu mapping file
def sd_build_cpu_map(sd_chart_list):
    data_link_map_list = []
    cp = re.compile(r'^\s+\d+\s+([a-zA-Z0-9_-]+)$') #find CPU name in file
    bg = re.compile(r'^\s+\d+\s+Connector list of the function packets') # find beginning of link information
    en = re.compile(r'^\s*\d+\s+\*')
    ch = re.compile(r'^\s*\d+\s+FP-([a-zA-Z0-9_\-@]+)')
    lk = re.compile(r'^\s*\d+\s+(\$[a-zA-Z0-9_\-@]+)\s+([\w]+)\s+((<)|(>))\s+([\w]+)\s+([a-zA-Z0-9_-]+)$')
    
    for i in sd_chart_list:
        for (k,v) in sd_chart_list[i].items():
            chart_lines = sd_open_chart(v)
            print("Parsing '%s' chart "%(k))
            cpu_mark = False
            beg_mark = False
            end_mark = False
            for l in chart_lines:
                ##Find CPU name
                if not cpu_mark:
                    cp_s = cp.search(l)
                    if cp_s :
                        cpu = cp_s.group(1)
                        cpu_mark = True
                        print(cpu)   
                else:
                    if not beg_mark:
                        if bg.search(l):
                            beg_mark = True
                    else:
                        #check end
                        if en.search(l):
                            end_mark = True
                            break
                        else:
                            #main block:
                            ch_s = ch.search(l)
                            if ch.search(l): #if chart beginning 1739	FP-MONIW1
                                chart = ch_s.group(1)
                            else:
                                lk_s = lk.search(l)
                                if lk_s: #if chart link definition 1744	   $DMALB1 T5 < PN     PN-D01_P1
                                    #'cpu','chart','out','link','cpu_source'
                                    data_link_map_list.append([cpu, chart.upper(),lk_s.group(3),lk_s.group(1),lk_s.group(7)])
    data_link_map_df = pd.DataFrame(data_link_map_list, columns=['cpu','chart','out','link','cpu_source'])
    return data_link_map_df

def sd_get_chart_cpu(data_link_map_df,chart):
    try:
        result = data_link_map_df[data_link_map_df['chart']==chart].iloc[0]['cpu']
    except IndexError:
        result = -1
    return result
def sd_get_block_link_source_cpu(data_link_map_df,link,chart):
    return data_link_map_df[(data_link_map_df['chart']==chart)&\
                            (data_link_map_df['link']==link)&\
                            (data_link_map_df['out']=="<")].iloc[0]['cpu_source']

def sd_get_link_partner(data_link_source_df,cpu_link):
    try:
        return data_link_source_df[(data_link_source_df['cpu_link']==cpu_link)].iloc[0]['chart_block_signal']
    except IndexError:
        return None
    

In [9]:
###########EXECUTION CELL###########
#creating row data DataFrame "data_s1" from chart list
   
data_lm = sd_build_cpu_map(sd_cpu_charts_list)
data_s1,data_ls1 = sd_build_data_s1(sd_chart_list,data_lm)
data_s1["block"] = data_s1["block"].astype(str)

data_s1

Parsing '1tx01' chart 
PN-D01_P1
Parsing '2tx01' chart 
PN-D04_P2
Parsing '3tx01' chart 
PN-D06_P3
Parsing '4tx01' chart 
PN-D08_P4
Parsing 'SCOI02' chart with 521 functions
Parsing 'SCOI92' chart with 271 functions
Parsing 'SDRFC2' chart with 47 functions
Parsing 'SERV_1' chart with 56 functions
Parsing 'SERV_2' chart with 21 functions
Parsing 'SERV_3' chart with 11 functions
Parsing 'SERV_4' chart with 29 functions
Parsing 'SIN_D2' chart with 223 functions
Parsing 'SIN__2' chart with 440 functions
Parsing 'SMES_2' chart with 134 functions
Parsing 'SMOD12' chart with 104 functions
Parsing 'SMOD22' chart with 100 functions
Parsing 'SMSR12' chart with 165 functions
Parsing 'SMSR22' chart with 102 functions
Parsing 'SOUTD2' chart with 127 functions
Parsing 'SOUT_2' chart with 720 functions
Parsing 'SPARA2' chart with 268 functions
Parsing 'SPOS12' chart with 94 functions
Parsing 'SPOS22' chart with 139 functions
Parsing 'SSDEF2' chart with 127 functions
Parsing 'SSIMU2' chart with 47 fun

signal type_base inout type_conv       value        cpu cpu_source  \
0          IS        V2     <      None     $DMOK02  PN-D04_P2  PN-D04_P2   
1          Q1        B1     >      None        None  PN-D04_P2  PN-D04_P2   
2          Q2        B1     >      None        None  PN-D04_P2  PN-D04_P2   
3          Q3        B1     >      None        None  PN-D04_P2  PN-D04_P2   
4          Q4        B1     >      None        None  PN-D04_P2  PN-D04_P2   
5          Q5        B1     >      None        None  PN-D04_P2  PN-D04_P2   
6          Q6        B1     >      None        None  PN-D04_P2  PN-D04_P2   
7          Q7        B1     >      None        None  PN-D04_P2  PN-D04_P2   
8          Q8        B1     >      None        None  PN-D04_P2  PN-D04_P2   
9          Q9        B1     >      None        None  PN-D04_P2  PN-D04_P2   
10        Q10        B1     >      None        None  PN-D04_P2  PN-D04_P2   
11        Q11        B1     >      None        None  PN-D04_P2  PN-D04_P2   
12        Q12        B1     >      None        None  PN-D04_P2  PN-D04_P2   
13        Q13        B1     >      None        None  PN-D04_P2  PN-D04_P2   
14        Q14        B1     >      None        None  PN-D04_P2  PN-D04_P2   
15        Q15        B1     >      None        None  PN-D04_P2  PN-D04_P2   
16        Q16        B1     >      None        None  PN-D04_P2  PN-D04_P2   
17         X1        NF     <      None          #4  PN-D04_P2  PN-D04_P2   
18         X2        NF     <      None          #6  PN-D04_P2  PN-D04_P2   
19          I        B1     <      None   PULDIA.Q3  PN-D04_P2  PN-D04_P2   
20          Y        NF     >      None        None  PN-D04_P2  PN-D04_P2   
21         I1        B1     <      None   PULDIA.Q4  PN-D04_P2  PN-D04_P2   
22         I2        B1     <      None  PULDIA.Q15  PN-D04_P2  PN-D04_P2   
23          Q        B1     >      None        None  PN-D04_P2  PN-D04_P2   
24          I        B1     <      None  PULDIA.Q16  PN-D04_P2  PN-D04_P2   
25          Q        B1     >      None        None  PN-D04_P2  PN-D04_P2   
26         I1        B1     <      None    NOTBEA.Q  PN-D04_P2  PN-D04_P2   
27         I2        B1     <      None           0  PN-D04_P2  PN-D04_P2   
28          Q        B1     >      None        None  PN-D04_P2  PN-D04_P2   
29          S        B1     <      None     PBPCS.Q  PN-D04_P2  PN-D04_P2   
...       ...       ...   ...       ...         ...        ...        ...   
114950     I5        B1     <      None  VCTX01.QTS  PN-D01_P1  PN-D01_P1   
114951     I6        B1     <      None  VITX01.QTS  PN-D01_P1  PN-D01_P1   
114952     I7        B1     <      None  VITX02.QTS  PN-D01_P1  PN-D01_P1   
114953     I8        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114954     I9        B1     <      None  VITX04.QTS  PN-D01_P1  PN-D01_P1   
114955    I10        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114956    I11        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114957    I12        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114958    I13        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114959    I14        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114960    I15        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114961    I16        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114962     QS        V2     >      None     $VBGT01  PN-D01_P1  PN-D01_P1   
114963     I1        B1     <      None   VMCRM.QTS  PN-D01_P1  PN-D01_P1   
114964     I2        B1     <      None   MMCRM.QTS  PN-D01_P1  PN-D01_P1   
114965     I3        B1     <      None     LI0.QTS  PN-D01_P1  PN-D01_P1   
114966     I4        B1     <      None     LI1.QTS  PN-D01_P1  PN-D01_P1   
114967     I5        B1     <      None     LI2.QTS  PN-D01_P1  PN-D01_P1   
114968     I6        B1     <      None     LI3.QTS  PN-D01_P1  PN-D01_P1   
114969     I7        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114

In [18]:
###########EXECUTION CELL###########
#save intermidiate result
data_a1.to_csv(os.path.join(PATH_TO_DATA,FILE_NAME_TEMP0))
data_s1.to_csv(os.path.join(PATH_TO_DATA,FILE_NAME_TEMP1))
data_ls1.to_csv(os.path.join(PATH_TO_DATA,FILE_NAME_TEMP2))
data_lm.to_csv(os.path.join(PATH_TO_DATA,FILE_NAME_TEMP3))


In [7]:
###########EXECUTION CELL###########
#restore intermediate result
data_a1 = pd.read_csv(os.path.join(PATH_TO_DATA,FILE_NAME_TEMP0),index_col=0)
data_s1 = pd.read_csv(os.path.join(PATH_TO_DATA,FILE_NAME_TEMP1),index_col=0)
data_ls1 = pd.read_csv(os.path.join(PATH_TO_DATA,FILE_NAME_TEMP2),index_col=0)
data_lm = pd.read_csv(os.path.join(PATH_TO_DATA,FILE_NAME_TEMP3),index_col=0)

In [10]:
###########LIBRARY CELL###########
#find partner link and put in 'value_linked' column.
#This column should be used for comparison
def sd_rect_data_s1(data_df,data_link_source_df):
    def lookup(x):
        partner = sd_get_link_partner(data_link_source_df,x)
        return partner
    data_df['value_linked'] = data_df['cpu_link'].apply(lookup)
    return data_df

#copy values in 'value_linked' - to get proper view: value or link to other block. 
#This column should be used for comparison
#Also convert in-chart link to absolute representation e.g. ENMESS.Q => MONIW1\ENMESS.Q
def sd_rect_data_s2(data_df):
    def lookup(x):
        if x['value_linked'] is None:
            if re.search(r'^[a-zA-Z0-9_\-@]+\.[a-zA-Z0-9_\-@]+$',str(x['value'])) and not re.search(r'^[0-9]+\.[0-9]+$',str(x['value'])):
                if not x['type_base'] in ['CR','NK','TR','RR']:
                    return x['chart']+"\\"+x['value']
                else:
                    return x['value']
            else:
                return x['value']
        else:
            return x['value_linked']
    data_df['value_linked'] = data_df.apply(lookup,axis = 1)
    return data_df



In [11]:
###########EXECUTION CELL###########
data_s2 = sd_rect_data_s1(data_s1.copy(),data_ls1)
data_s3 = sd_rect_data_s2(data_s2.copy())
data_s3

signal type_base inout type_conv       value        cpu cpu_source  \
0          IS        V2     <      None     $DMOK02  PN-D04_P2  PN-D04_P2   
1          Q1        B1     >      None        None  PN-D04_P2  PN-D04_P2   
2          Q2        B1     >      None        None  PN-D04_P2  PN-D04_P2   
3          Q3        B1     >      None        None  PN-D04_P2  PN-D04_P2   
4          Q4        B1     >      None        None  PN-D04_P2  PN-D04_P2   
5          Q5        B1     >      None        None  PN-D04_P2  PN-D04_P2   
6          Q6        B1     >      None        None  PN-D04_P2  PN-D04_P2   
7          Q7        B1     >      None        None  PN-D04_P2  PN-D04_P2   
8          Q8        B1     >      None        None  PN-D04_P2  PN-D04_P2   
9          Q9        B1     >      None        None  PN-D04_P2  PN-D04_P2   
10        Q10        B1     >      None        None  PN-D04_P2  PN-D04_P2   
11        Q11        B1     >      None        None  PN-D04_P2  PN-D04_P2   
12        Q12        B1     >      None        None  PN-D04_P2  PN-D04_P2   
13        Q13        B1     >      None        None  PN-D04_P2  PN-D04_P2   
14        Q14        B1     >      None        None  PN-D04_P2  PN-D04_P2   
15        Q15        B1     >      None        None  PN-D04_P2  PN-D04_P2   
16        Q16        B1     >      None        None  PN-D04_P2  PN-D04_P2   
17         X1        NF     <      None          #4  PN-D04_P2  PN-D04_P2   
18         X2        NF     <      None          #6  PN-D04_P2  PN-D04_P2   
19          I        B1     <      None   PULDIA.Q3  PN-D04_P2  PN-D04_P2   
20          Y        NF     >      None        None  PN-D04_P2  PN-D04_P2   
21         I1        B1     <      None   PULDIA.Q4  PN-D04_P2  PN-D04_P2   
22         I2        B1     <      None  PULDIA.Q15  PN-D04_P2  PN-D04_P2   
23          Q        B1     >      None        None  PN-D04_P2  PN-D04_P2   
24          I        B1     <      None  PULDIA.Q16  PN-D04_P2  PN-D04_P2   
25          Q        B1     >      None        None  PN-D04_P2  PN-D04_P2   
26         I1        B1     <      None    NOTBEA.Q  PN-D04_P2  PN-D04_P2   
27         I2        B1     <      None           0  PN-D04_P2  PN-D04_P2   
28          Q        B1     >      None        None  PN-D04_P2  PN-D04_P2   
29          S        B1     <      None     PBPCS.Q  PN-D04_P2  PN-D04_P2   
...       ...       ...   ...       ...         ...        ...        ...   
114950     I5        B1     <      None  VCTX01.QTS  PN-D01_P1  PN-D01_P1   
114951     I6        B1     <      None  VITX01.QTS  PN-D01_P1  PN-D01_P1   
114952     I7        B1     <      None  VITX02.QTS  PN-D01_P1  PN-D01_P1   
114953     I8        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114954     I9        B1     <      None  VITX04.QTS  PN-D01_P1  PN-D01_P1   
114955    I10        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114956    I11        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114957    I12        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114958    I13        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114959    I14        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114960    I15        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114961    I16        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114962     QS        V2     >      None     $VBGT01  PN-D01_P1  PN-D01_P1   
114963     I1        B1     <      None   VMCRM.QTS  PN-D01_P1  PN-D01_P1   
114964     I2        B1     <      None   MMCRM.QTS  PN-D01_P1  PN-D01_P1   
114965     I3        B1     <      None     LI0.QTS  PN-D01_P1  PN-D01_P1   
114966     I4        B1     <      None     LI1.QTS  PN-D01_P1  PN-D01_P1   
114967     I5        B1     <      None     LI2.QTS  PN-D01_P1  PN-D01_P1   
114968     I6        B1     <      None     LI3.QTS  PN-D01_P1  PN-D01_P1   
114969     I7        B1     <      None           1  PN-D01_P1  PN-D01_P1   
114

In [14]:
#data_s2[~data_s2['value_linked'].isnull()]

In [251]:
#data_s3[~data_s3['cpu_link'].isnull()]

In [80]:
################TEST CELL#############
test_df = data_s3.copy()
#test_df[test_df['link'].apply(lambda x: bool(re.search(r"\$\w+\s+\w+",str(x)))==True)]
#test_df = data_ls1.copy()
#test_df[test_df['link'].apply(lambda x: bool(any("$" in s for s in x) and len(x)>1)==True)]
#test_df[(test_df['cpu_link']=='PN-D01_P1_$VISW17')]
#test_df[(test_df['type_base']=='PN-D01_P1_$VISW17')]
test_df['type_base'].unique()
##array(['B1', 'TF', 'N2', 'V2', 'MR', 'NS', 'O2', 'CR', 'V4', 'NF', 'V1',
#       'I2', 'NK', 'TR', 'N4', 'RR'], dtype=object)
#SD types:
#'B1' - BOOL (0/1/link)
#'TF' - Time (ffff.fff[s/min/S/ms])
#'N2' - Integer (ddddd)
#'V2' - Integer HEX
#'MR' - Message link (e.g MESY_1)(Inout = "-")
#'NS' - String (Inout = "-")
#'O2' - Integer (dddddd)
#'CR' - Hardware connectors, string
#'V4' - Dword HEX
#'NF' - Floating point
#'V1' - Byte HEX   
#'I2' - Integer
#'NK' - Hardware connectors, string (Inout = "=")
#'TR' - Telegram transmit connector e.g. !EXM504 (Inout = "=")
#'N4' - Integer 32 bits (%/HEX/ddd)
#'RR' - Telegram recieve connector e.g. !T4EX05 (Inout = "=")

#filt_type_base = ['B1','TF','N2','V2','O2','V4','NF','V1','I2','TR','RR']
filt_type_base = ['V2']
filt_inout = ['<','=']
#&~(test_df['type_conv'].isin(['O2','V2','N2','I2']))
test_df[(test_df['type_base'].isin(filt_type_base))&~(test_df['type_conv'].isnull())&(test_df['inout'].isin(filt_inout))] #&~(test_df['type_conv'].isnull())

test_df[test_df['block']=="RPALL"]


signal type_base inout type_conv     value        cpu cpu_source  \
87        X1        N2     <        O2       036  PN-D01_P1  PN-D01_P1   
88        X2        N2     <        O2       036  PN-D01_P1  PN-D01_P1   
89         I        B1     <       NaN         0  PN-D01_P1  PN-D01_P1   
90         Y        N2     >        O2  'RP_ALL'  PN-D01_P1  PN-D01_P1   
631       X1        N2     <        O2       038  PN-D05_P2  PN-D05_P2   
632       X2        N2     <        O2       038  PN-D05_P2  PN-D05_P2   
633        I        B1     <       NaN         0  PN-D05_P2  PN-D05_P2   
634        Y        N2     >        O2  'RP_ALL'  PN-D05_P2  PN-D05_P2   
23859     X1        N2     <        O2       036  PN-D01_P1  PN-D01_P1   
23860     X2        N2     <        O2       036  PN-D01_P1  PN-D01_P1   
23861      I        B1     <       NaN         0  PN-D01_P1  PN-D01_P1   
23862      Y        N2     >        O2  'RP_All'  PN-D01_P1  PN-D01_P1   
25083     X1        N2     <        O2       038  PN-D05_P2  PN-D05_P2   
25084     X2        N2     <        O2       038  PN-D05_P2  PN-D05_P2   
25085      I        B1     <       NaN         0  PN-D05_P2  PN-D05_P2   
25086      Y        N2     >        O2  'RP_All'  PN-D05_P2  PN-D05_P2   
25279     X1        N2     <        O2       036  PN-D01_P1  PN-D01_P1   
25280     X2        N2     <        O2       036  PN-D01_P1  PN-D01_P1   
25281      I        B1     <       NaN         0  PN-D01_P1  PN-D01_P1   
25282      Y        N2     >        O2  'RP_ALL'  PN-D01_P1  PN-D01_P1   
25713     X1        N2     <        O2       038  PN-D05_P2  PN-D05_P2   
25714     X2        N2     <        O2       038  PN-D05_P2  PN-D05_P2   
25715      I        B1     <       NaN         0  PN-D05_P2  PN-D05_P2   
25716      Y        N2     >        O2  'RP_ALL'  PN-D05_P2  PN-D05_P2   

      cpu_link   chart  block  \
87         NaN  MONIW1  RPALL   
88         NaN  MONIW1  RPALL   
89         NaN  MONIW1  RPALL   
90         NaN  MONIW1  RPALL   
631        NaN  MONIW2  RPALL   
632        NaN  MONIW2  RPALL   
633        NaN  MONIW2  RPALL   
634        NaN  MONIW2  RPALL   
23859      NaN  MESY_1  RPALL   
23860      NaN  MESY_1  RPALL   
23861      NaN  MESY_1  RPALL   
23862      NaN  MESY_1  RPALL   
25083      NaN  MESY_2  RPALL   
25084      NaN  MESY_2  RPALL   
25085      NaN  MESY_2  RPALL   
25086      NaN  MESY_2  RPALL   
25279      NaN  MONIM1  RPALL   
25280      NaN  MONIM1  RPALL   
25281      NaN  MONIM1  RPALL   
25282      NaN  MONIM1  RPALL   
25713      NaN  MONIM2  RPALL   
25714      NaN  MONIM2  RPALL   
25715      NaN  MONIM2  RPALL   
25716      NaN  MONIM2  RPALL   

                                                    link value_linked  
87                                                    []          036  
88                                                    []          036  
89                                                    []            0  
90     ['MES039.RP', 'MES040.RP', 'MES036.RP', 'MES03...     'RP_ALL'  
631                                                   []          038  
632                                                   []          038  
633                                                   []            0  
634    ['MES039.RP', 'MES040.RP', 'MES036.RP', 'MES03...     'RP_ALL'  
23859                                                 []          036  
23860                                                 []          036  
23861                                                 []            0  
23862  ['SEND21.RP', 'SEND12.RP', 'SEND15.RP', 'SEND1...     'RP_All'  
25083                                                 []          038  
25084                                                 []          038  
25085                                                 []            0  
25086  ['SEND12.RP', 'SEND03.RP', 'SEND06.RP', 'SEND0...     'RP_All'  
25279                                                 []          036  
25280                            

In [41]:
###########LIBRARY CELL###########
#report generator of comparison of block in all SD and TDC charts
def report_find_miss_blocks (data_sd,data_tdc, to_file = True, timestamp = datetime.datetime.now()):
    README_HEADER = COMPARATOR_README +"\
\r\nReport: find missing blocks in TDC program\
\r\nDate ant time of report generation: %s \
\r\n===================================================================================\
\r\n"%(str(timestamp))
    
    def generate_report(f):
        print(README_HEADER,file = f) 
        chartblock_sel = data_sd["chart"]+"/"+data_sd["block"]
        sd_uniq_blocks = chartblock_sel.unique()
        tdc_uniq_blocks = data_tdc['chartblock'].unique()
        for i in sd_uniq_blocks:
            if not i in tdc_uniq_blocks:
                print("Missing block in TDC: ",i,"\r\n",file = f) 
        
        
        
    if to_file:
        file_suffix = "@_compare_blocks_sd_%s"%(str(timestamp.date()))
        file_prefix = "report_@"
        try:
            # Create target Directory
            os.mkdir(os.path.join(PATH_TO_REPORTS))
        except FileExistsError:
            pass
        #sys.stdout = open(os.path.join(PATH_TO_REPORTS,(file_prefix+FILE_NAME_DATA1.split(".")[0]+file_suffix+".txt")), 'w')
        with open(os.path.join(PATH_TO_REPORTS,(file_prefix+FILE_NAME_DATA1.split(".")[0]+file_suffix+".txt")), 'w') as f: 
            generate_report(f)
    else:
        generate_report(sys.stdout)

In [42]:
#############EXECUTION GENERATE REPORT report_find_miss_blocks############
report_find_miss_blocks(data_s2,data_a1,to_file = True)

In [43]:
###########LIBRARY CELL###########
#####report of comparison of all SD blocks inputs, including links

        #['BOOL' 'INT' 'WORD' 'SDTIME' 'GLOBAL' 'STRING' 'REAL' 'DINT' 'BYTE' 'DWORD']
        #SD types:
        #'B1' - BOOL (0/1/link)
        #'TF' - Time (ffff.fff[s/min/S/ms])
        #'N2' - Integer (ddddd)
        #'V2' - Integer HEX
        #'MR' - Message link (e.g MESY_1)(Inout = "-")
        #'NS' - String (Inout = "-")
        #'O2' - Integer (dddddd)
        #'CR' - Hardware connectors, string
        #'V4' - Dword HEX
        #'NF' - Floating point
        #'V1' - Byte HEX   
        #'I2' - Integer
        #'NK' - Hardware connectors, string (Inout = "=")
        #'TR' - Telegram transmit connector e.g. !EXM504 (Inout = "=")
        #'N4' - Integer 32 bits (%/HEX/ddd)
        #'RR' - Telegram recieve connector e.g. !T4EX05 (Inout = "=") 
        
#report parameters    
filt_type_base = ['B1','TF','N2','N4','V2','O2','V4','NF','V1','I2','TR','RR']  #,'NS'
filt_inout = ['<']#'=','-'

def report_comp_inputs (inp_data_sd,inp_data_tdc, to_file = True, timestamp = datetime.datetime.now()):
    README_HEADER = COMPARATOR_README +"\
\r\nReport: compare all SD inputs (including links) with TDC program\
\r\nDate ant time of report generation: %s \
\r\n===================================================================================\
\r\n"%(str(timestamp))
    data_sd = inp_data_sd.copy()
    data_tdc = inp_data_tdc.copy()
    def merge_tdc_link_value(l_value,l_link):
        if pd.isnan(l_link):
            return l_link
        else:
            return l_value
    
    def clean_sd_tdc_str_values(s_value,a_value,sd_type,sd_type_conv,chart_block_signal,f):
        #modify HEX function
        def twos_complement(hexstr,bits,base=16):
            value = int(hexstr,base)
            if value & (1 << (bits-1)):
                value -= 1 << bits
            return value
 
        #for debugging
        #print("Working on:",s_value,a_value,sd_type,sd_type_conv)
        
        #check if values are empty
        if  pd.isnull(s_value):
            if pd.isnull(a_value):
                return True
            else:
                return False
        else:
            if pd.isnull(a_value):
                return False
        #regex for chart and link $ 
        con_check = re.compile(r'^[a-zA-Z0-9_\-@]+\\[a-zA-Z0-9_\-@]+\.[a-zA-Z0-9_\-@]+$')
        link_check = re.compile(r'^\$')
        link_check2 = re.compile(r'^\!')
        #check if SD is link
        #print("s_value:",s_value)
        #print("a_value:",a_value)
        if con_check.search(s_value) or link_check.search(s_value) or link_check2.search(s_value) \
        or ("'" in s_value):
            #print("Signal value of simadyn has chart connection")
            a_value_res=a_value
            s_value_res=s_value
        else:
            if con_check.search(a_value) or link_check.search(a_value) or link_check2.search(a_value):
                #Sd is value but TDC is a link
                a_value_res=a_value
                s_value_res=s_value
            else:
                #SD and TDC are normal values
                if sd_type=='NF':
                    a_value_res = float(a_value.replace(',','.'))
                    if '%' in s_value.split("[")[0]:
                        s_value_res = float(re.sub('[^0-9.E-]','', s_value.split("[")[0]))*0.01
                    else:
                        if sd_type_conv == 'TF':
                            units = 1000
                            un_txt = s_value.lower()
                            un_txt = un_txt.split("[")[1]
                            un_txt = un_txt.split("]")[0]
                            if un_txt=="s":
                                units = 1000
                            elif un_txt=="min":
                                units = 60000
                            elif un_txt=="ms":
                                units = 1
                            tmp_txt = re.sub('[^0-9.E-]','', s_value)
                            s_value_res = int(math.floor(float(tmp_txt)*units))
                        else: 
                            if "[" in s_value:
                                s_value_res = float(re.sub('[^0-9.E-]','', s_value.split("[")[0]))
                            else:
                                s_value_res = float(re.sub('[^0-9.E-]','', s_value))  
                elif sd_type=='B1':
                    if re.match(r'[10]$', s_value.strip()):
                        s_value_res = bool(int(s_value))
                    else:
                        raise
                    a_value_res = bool(int(a_value))
                elif sd_type=='TF': 
                    a_value_res = int(a_value.strip('ms'))
                    units = 1000
                    un_txt = s_value.lower()
                    un_txt = un_txt.split("[")[1]
                    un_txt = un_txt.split("]")[0]
                    if un_txt=="s":
                        units = 1000
                    elif un_txt=="min":
                        units = 60000
                    elif un_txt=="ms":
                        units = 1
                    tmp_txt = re.sub('[^0-9.E-]','', s_value)
                    s_value_res = int(math.floor(float(tmp_txt)*units))

                elif sd_type in ['N2','N4','V2','O2','V4','V1','I2']:
                    #edit TDC value
                    if "16#" in a_value:
                        tmp_txt = a_value.split('16#')[1]
                        a_value_res = twos_complement(tmp_txt.strip(),16)    
                    else:
                        a_value_res = int(a_value)
                    #prepare SD value    
                    if "H" in s_value:
                        tmp_txt = s_value.split('0H')[1]
                        s_value_res = twos_complement(tmp_txt.strip(),16)
                    elif '%' in s_value:
                        s_value_res = int(round(float(re.sub('[^0-9.E-]','', s_value))*16384*0.01))
                    elif "B" in s_value:
                        tmp_txt = s_value.split('0B')[1]
                        tmp_txt =  tmp_txt.replace(" ", "")
                        s_value_res = twos_complement(tmp_txt.strip(),16,base = 2)
                    else:
                        s_value_res = int(re.sub('[^0-9.E-]','', s_value))   
                elif sd_type in ['TR','RR','NS','MR','CR']:
                    a_value_res = a_value.strip("'")
                    s_value_res = s_value.strip("'")
                elif sd_type in ['NK']:
                    a_value_res = a_value.strip("*")
                    s_value_res = s_value.strip("*")
                else:
                    print("\r\nFault in:",s_value,a_value,sd_type,sd_type_conv)
                    raise
        if not isinstance(s_value_res, str):
            if float(a_value_res)!=0 and float(s_value_res)!=0:
                result = abs((float(s_value_res)-float(a_value_res))/float(s_value_res))<0.005
            else:
                result = s_value_res==a_value_res
        else:
            result = s_value_res==a_value_res
        if not result:
            print("\r\nDifference found in: ",chart_block_signal,"SD/TDC value:",s_value_res,'==>>> ',a_value_res,file = f)
        return result

    def generate_report(f):
        print(README_HEADER,file = f) 
        #this comparator works with following data types and connectors:
        #filter sd data frame
        data_sd_filtered = data_sd[(data_sd['type_base'].isin(filt_type_base))&(data_sd['inout'].isin(filt_inout))]
        
        #connect links $XXXXX->$XXXXX
        d = dict(zip(data_tdc['chart_block_signal'].values, data_tdc['value_linked'].values))
        data_sd_filtered['chart_block_signal'] = data_sd_filtered["chart"]+"/"+data_sd_filtered["block"]+"."+data_sd_filtered["signal"]
        
        data_sd_filtered['val_tdc'] = data_sd_filtered['chart_block_signal'].map(d)
        data_sd_filtered['compare_val_sd'] = data_sd_filtered.apply(lambda row: clean_sd_tdc_str_values(\
           row['value_linked'], row['val_tdc'],row['type_base'], row['type_conv'],row['chart_block_signal'],f), axis=1)
      
    if to_file:
        file_suffix = "@_compare_inputs_sd_%s"%(str(timestamp.date()))
        file_prefix = "report_@"
        try:
            # Create target Directory
            os.mkdir(os.path.join(PATH_TO_REPORTS))
        except FileExistsError:
            pass
        #sys.stdout = open(os.path.join(PATH_TO_REPORTS,(file_prefix+FILE_NAME_DATA1.split(".")[0]+file_suffix+".txt")), 'w')
        with open(os.path.join(PATH_TO_REPORTS,(file_prefix+FILE_NAME_DATA1.split(".")[0]+file_suffix+".txt")), 'w') as f: 
            generate_report(f)
    else:
        generate_report(sys.stdout)


    
#test_df = data_s2.head(5000).copy()

In [44]:
#############EXECUTION GENERATE REPORT report_comp_inputs############
report_comp_inputs(data_s3,data_a1,to_file = True)


In [18]:
#data_s3.iloc[72115:72130]

In [19]:
#re.search(r'^\!',"!AABDUA.00123")

In [109]:
#/////////////////TEST CELL/////////////////////
test_sd = data_s3.copy()
test_a1 = data_a1.copy()
def merge_tdc_link_value(l_value,l_link):
    if pd.isnan(l_link):
        return l_link
    else:
        return l_value
def clean_sd_tdc_str_values(s_value,a_value,sd_type,sd_type_conv):
    #modify HEX function
    def twos_complement(hexstr,bits,base=16):
        value = int(hexstr,base)
        if value & (1 << (bits-1)):
            value -= 1 << bits
        return value
    #['BOOL' 'INT' 'WORD' 'SDTIME' 'GLOBAL' 'STRING' 'REAL' 'DINT' 'BYTE' 'DWORD']
    #SD types:
    #'B1' - BOOL (0/1/link)
    #'TF' - Time (ffff.fff[s/min/S/ms])
    #'N2' - Integer (ddddd)
    #'V2' - Integer HEX
    #'MR' - Message link (e.g MESY_1)(Inout = "-")
    #'NS' - String (Inout = "-")
    #'O2' - Integer (dddddd)
    #'CR' - Hardware connectors, string
    #'V4' - Dword HEX
    #'NF' - Floating point
    #'V1' - Byte HEX   
    #'I2' - Integer
    #'NK' - Hardware connectors, string (Inout = "=")
    #'TR' - Telegram transmit connector e.g. !EXM504 (Inout = "=")
    #'N4' - Integer 32 bits (%/HEX/ddd)
    #'RR' - Telegram recieve connector e.g. !T4EX05 (Inout = "=")  
    #for debugging
    print("Working on:",s_value,a_value,sd_type,sd_type_conv)
    #check if values are empty
    if s_value != s_value:
        if a_value != a_value:
            return True
        else:
            return False
    else:
        if a_value != a_value:
            return False
           
    #regex for chart and link $ 
    con_check = re.compile(r'^[a-zA-Z0-9_\-@]+\\[a-zA-Z0-9_\-@]+\.[a-zA-Z0-9_\-@]+$')
    link_s_check = re.compile(r'^\$')
    link_a_check = re.compile(r'^!')
    #check if SD is link
    if con_check.search(s_value) or link_s_check.search(s_value) or ("'" in s_value):
        #print("Signal value of simadyn has chart connection")
        a_value_res=a_value
        s_value_res=s_value
    else:
        if con_check.search(a_value) or link_a_check.search(a_value):
            #Sd is value but TDC is a link
            a_value_res=a_value
            s_value_res=s_value
        else:
            #SD and TDC are normal values
            if sd_type=='NF':
                a_value_res = float(a_value.replace(',','.'))
                if '%' in s_value:
                    s_value_res = float(re.sub('[^0-9.E-]','', s_value))*0.01
                else:
                    s_value_res = float(re.sub('[^0-9.E-]','', s_value))
            elif sd_type=='B1':
                if re.match(r'[10]$', s_value.strip()):
                    s_value_res = bool(int(s_value))
                else:
                    raise
                a_value_res = bool(int(a_value))
            elif sd_type=='TF': 
                a_value_res = int(a_value.strip('ms'))
                units = 1000
                un_txt = s_value.lower()
                un_txt = un_txt.split("[")[1]
                un_txt = un_txt.split("]")[0]
                if un_txt=="s":
                    units = 1000
                elif un_txt=="min":
                    units = 60000
                elif un_txt=="ms":
                    units = 1
                tmp_txt = re.sub('[^0-9.E-]','', s_value)
                s_value_res = int(math.floor(float(tmp_txt)*units))

            elif sd_type in ['N2','N4','V2','O2','V4','V1','I2']:
                #edit TDC value
                if "16#" in a_value:
                    tmp_txt = a_value.split('16#')[1]
                    a_value_res = twos_complement(tmp_txt.strip(),16)    
                else:
                    a_value_res = int(a_value)
                #prepare SD value    
                if "H" in s_value:
                    tmp_txt = s_value.split('0H')[1]
                    s_value_res = twos_complement(tmp_txt.strip(),16)
                elif '%' in s_value:
                    s_value_res = int(round(float(re.sub('[^0-9.E-]','', s_value))*16384*0.01))
                elif "B" in s_value:
                    tmp_txt = s_value.split('0B')[1]
                    tmp_txt =  tmp_txt.replace(" ", "")
                    s_value_res = twos_complement(tmp_txt.strip(),16,base = 2)
                else:
                    s_value_res = int(re.sub('[^0-9.E-]','', s_value))   
            elif sd_type in ['TR','RR','NS','MR','CR']:
                a_value_res = a_value.strip("'")
                s_value_res = s_value.strip("'")
            elif sd_type in ['NK']:
                a_value_res = a_value.strip("*")
                s_value_res = s_value.strip("*")
            else:
                print("Fault in:",s_value,a_value,sd_type,sd_type_conv)
                raise
    print("Out: ",s_value_res,a_value_res,'==>>>',s_value_res==a_value_res)
    return s_value_res==a_value_res
    
    
    
test_a1['value_linked'] = np.where(test_a1['link'].isnull(), test_a1['value'],test_a1['link'] )
#test_a1['value_linked'] = test_a1.apply(lambda row: merge_tdc_link_value(row['value'], row['link']), axis=1)
d = dict(zip(test_a1['chart_block_signal'].values, test_a1['value_linked'].values))
test_sd['chart_block_signal'] = test_sd["chart"]+"/"+test_sd["block"]+"."+test_sd["signal"]
test_sd['val_tdc'] = test_sd['chart_block_signal'].map(d)
#test_sd[test_sd['inout']=='<'].iloc[200:300]
#test_sd[(test_sd['inout']=='<')&(test_sd['value_linked']!=test_sd['tdc_value'])]
filt_inout = ['<','=','-']
test_sd_filtered = test_sd[(test_sd['inout'].isin(filt_inout))]
test_sd_filtered['compare_val_sd'] = test_sd_filtered.apply(lambda row: clean_sd_tdc_str_values(\
   row['value_linked'], row['val_tdc'],row['type_base'], row['type_conv']), axis=1)
test_sd_filtered

Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: 60[s] 60000ms TF nan
Out:  60000 60000 ==>>> True
Working on: 0H0 0 N2 V2
Out:  0 0 ==>>> True
Working on: ENIHW1\VIHW36.QS ENIHW1\VIHW36.QS N2 V2
Out:  ENIHW1\VIHW36.QS ENIHW1\VIHW36.QS ==>>> True
Working on: MONIW1\ENMESS.Q MONIW1\ENMESS.Q B1 nan
Out:  MONIW1\ENMESS.Q MONIW1\ENMESS.Q ==>>> True
Working on: 0H0 0 N2 V2
Out:  0 0 ==>>> True
Working on: ENOHW1\VOHW01.QS ENOHW1\VOHW01.QS N2 V2
Out:  ENOHW1\VOHW01.QS ENOHW1\VOHW01.QS ==>>> True
Working on: MONIW1\ENMESS.Q MONIW1\ENMESS.Q B1 nan
Out:  MONIW1\ENMESS.Q MONIW1\ENMESS.Q ==>>> True
Working on: MONIW1\NSW000.Y MONIW1\NSW000.Y V2 nan
Out:  MONIW1\NSW000.Y MONIW1\NSW000.Y ==>>> True
Working on: MONIW1\NSW001.Y MONIW1\NSW001.Y V2 nan
Out:  MONIW1\NSW001.Y MONIW1\NSW001.Y ==>>> True
Working on: 0H0 0 N2 V2
Out:  0 0 ==>>> True
Working on: ENISW1\VISW01.QS ENISW1\VISW01.QS N2 V2
Out:  ENISW1\VISW01.QS ENISW1\VISW01.QS ==>>> True
Working on: MONIW1\ENMESS.Q MONIW1\ENMESS.Q 

Working on: ENIHW1\T3EN04.YEV ENIHW1\T3EN04.YEV N2 O2
Out:  ENIHW1\T3EN04.YEV ENIHW1\T3EN04.YEV ==>>> True
Working on: MESY_1 MESY_1 MR nan
Out:  MESY_1 MESY_1 ==>>> True
Working on: '@C@85@ EN: Communication error receive !DMENW0' '@C@85@ EN: Communication error receive !DMENW0' NS nan
Out:  '@C@85@ EN: Communication error receive !DMENW0' '@C@85@ EN: Communication error receive !DMENW0' ==>>> True
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: MONIW1\RPALL.Y MONIW1\RPALL.Y O2 nan
Out:  MONIW1\RPALL.Y MONIW1\RPALL.Y ==>>> True
Working on: MONIW1\RSCOM.Y nan O2 nan
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: MONIW1\VIHW36.Q11 0 B1 nan
Out:  MONIW1\VIHW36.Q11 0 ==>>> False
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: ENIHW1\T3EN05.YEV 0 N2 O2
Out:  ENIHW1\T3EN05.YEV 0 ==>>> False
Working on: MESY_1 MESY_1 MR nan
Out:  MESY_1 MESY_1 ==>>> True
Working on: '@C@85@ EN: Communication error receive !DMENW0' '@C@85@ EN: Communication error r

Out:  MONIW1\VOHW01.Q2 MONIW1\VOHW01.Q2 ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: ENOHW1\ENE104.YEV ENOHW1\ENE104.YEV N2 O2
Out:  ENOHW1\ENE104.YEV ENOHW1\ENE104.YEV ==>>> True
Working on: MESY_1 MESY_1 MR nan
Out:  MESY_1 MESY_1 ==>>> True
Working on: '@C@85@ EN: Communication error send !ENE107' '@C@85@ EN: Communication error send !ENE107' NS nan
Out:  '@C@85@ EN: Communication error send !ENE107' '@C@85@ EN: Communication error send !ENE107' ==>>> True
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: MONIW1\RPALL.Y MONIW1\RPALL.Y O2 nan
Out:  MONIW1\RPALL.Y MONIW1\RPALL.Y ==>>> True
Working on: MONIW1\RSCOM.Y nan O2 nan
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: MONIW1\VOHW01.Q3 MONIW1\VOHW01.Q3 B1 nan
Out:  MONIW1\VOHW01.Q3 MONIW1\VOHW01.Q3 ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: ENOHW1\ENE107.YEV ENOHW1\ENE107.YEV N2 O2
Out:  ENOHW1\ENE107.YEV ENOHW1\ENE107.YEV ==>>> True
Working o

Working on: 0 0 N2 O2
Out:  0 0 ==>>> True
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: 60[s] 60000ms TF nan
Out:  60000 60000 ==>>> True
Working on: 0H0 0 N2 V2
Out:  0 0 ==>>> True
Working on: EXIHW2\VIHW01.QS EXIHW2\VIHW01.QS N2 V2
Out:  EXIHW2\VIHW01.QS EXIHW2\VIHW01.QS ==>>> True
Working on: MONIW2\ENMESS.Q MONIW2\ENMESS.Q B1 nan
Out:  MONIW2\ENMESS.Q MONIW2\ENMESS.Q ==>>> True
Working on: 0H0 0 N2 V2
Out:  0 0 ==>>> True
Working on: EXOHW2\VOHW01.QS EXOHW2\VOHW01.QS N2 V2
Out:  EXOHW2\VOHW01.QS EXOHW2\VOHW01.QS ==>>> True
Working on: MONIW2\ENMESS.Q MONIW2\ENMESS.Q B1 nan
Out:  MONIW2\ENMESS.Q MONIW2\ENMESS.Q ==>>> True
Working on: MONIW2\NSW000.Y MONIW2\NSW000.Y V2 nan
Out:  MONIW2\NSW000.Y MONIW2\NSW000.Y ==>>> True
Working on: MONIW2\NSW001.Y MONIW2\NSW001.Y V2 nan
Out:  MONIW2\NSW001.Y MONIW2\NSW001.Y ==>>> True
Working on: 0H0 0 N2 V2
Out:  0 0 ==>>> True
Working on: EXISW2\VISW01.QS EXISW2\VISW01.QS N2 V2
Out:  EXISW2\VISW01.QS EXISW2\VISW01.QS ==>>> True
W

Working on: MONIW2\VIHW01.Q6 MONIW2\VIHW01.Q6 B1 nan
Out:  MONIW2\VIHW01.Q6 MONIW2\VIHW01.Q6 ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: EXIHW2\CRV209.YEV EXIHW2\CRV209.YEV N2 O2
Out:  EXIHW2\CRV209.YEV EXIHW2\CRV209.YEV ==>>> True
Working on: MESY_2 MESY_2 MR nan
Out:  MESY_2 MESY_2 ==>>> True
Working on: '@C@88@ EX: Communication error receive !E2EX10' '@C@88@ EX: Communication error receive !E2EX10' NS nan
Out:  '@C@88@ EX: Communication error receive !E2EX10' '@C@88@ EX: Communication error receive !E2EX10' ==>>> True
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: MONIW2\RPALL.Y MONIW2\RPALL.Y O2 nan
Out:  MONIW2\RPALL.Y MONIW2\RPALL.Y ==>>> True
Working on: MONIW2\RSCOM.Y nan O2 nan
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: MONIW2\VIHW01.Q7 MONIW2\VIHW01.Q7 B1 nan
Out:  MONIW2\VIHW01.Q7 MONIW2\VIHW01.Q7 ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: EXIHW2\CRV210.YEV EXIHW2\CRV210.YEV N2 

...

Out:  ENOSW1\VMB_07.Q10 ENOSW1\VMB_07.Q10 ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: 0HFFFF 16#FFFF V2 nan
Out:  -1 -1 ==>>> True
Working on: 0H0000 16#0000 V2 nan
Out:  0 0 ==>>> True
Working on: 0H0000 16#0000 V2 nan
Out:  0 0 ==>>> True
Working on: 0H0000 16#0000 V2 nan
Out:  0 0 ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: ENOSW1\BSC028.QS ENOSW1\BSC028.QS V2 

Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: 0% 0 N2 nan
Out:  0 0 ==>>> True
Working on: !ENMCB1 !ENMCB1 TR nan
Out:  !ENMCB1 !ENMCB1 ==>>> True
Working on: D2303B D1904C.XFO CR nan
Out:  D2303B D1904C.XFO ==>>> False
Working on: 'ENMCB1' 'ENMCB1' NS nan
Out:  'ENMCB1' 'ENMCB1' ==>>> True
Working on: 'R' 'R' NS nan
Out:  'R' 'R' ==>>> True
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: ENOSW1\ENMCB1.QTS ENOSW1\ENMCB1.QTS B1

Out:  ENCC_1\VCC_11.QS ENCC_1\VCC_11.QS ==>>> True
Working on: ENCC_1\VCC12.QS ENCC_1\VCC12.QS V2 nan
Out:  ENCC_1\VCC12.QS ENCC_1\VCC12.QS ==>>> True
Working on: ENISW1\VISW05.QS ENISW1\VISW05.QS V2 nan
Out:  ENISW1\VISW05.QS ENISW1\VISW05.QS ==>>> True
Working on: ENISW1\VISW12.QS ENISW1\VISW12.QS V2 nan
Out:  ENISW1\VISW12.QS ENISW1\VISW12.QS ==>>> True
Working on: ENISW1\VISW13.QS ENISW1\VISW13.QS V2 nan
Out:  ENISW1\VISW13.QS ENISW1\VISW13.QS ==>>> True
Working on: ENISW1\VISW15.QS ENISW1\VISW15.QS V2 nan
Out:  ENISW1\VISW15.QS ENISW1\VISW15.QS ==>>> True
Working on: ENIHW1\VIHW14.QS ENIHW1\VIHW14.QS V2 nan
Out:  ENIHW1\VIHW14.QS ENIHW1\VIHW14.QS ==>>> True
Working on: ENBEA1\VIHW14.Q14 ENBEA1\VIHW14.Q14 B1 nan
Out:  ENBEA1\VIHW14.Q14 ENBEA1\VIHW14.Q14 ==>>> True
Working on: ENBEA1\VIHW14.Q16 ENBEA1\VIHW14.Q16 B1 nan
Out:  ENBEA1\VIHW14.Q16 ENBEA1\VIHW14.Q16 ==>>> True
Working on: ENBEA1\VIHW14.Q15 ENBEA1\VIHW14.Q15 B1 nan
Out:  ENBEA1\VIHW14.Q15 ENBEA1\VIHW14.Q15 ==>>> True
Worki

Out:  False False ==>>> True
Working on: 0 0 B1 nan
Out:  False False ==>>> True
Working on: #500[ms] 500 NF nan
Out:  500.0 500.0 ==>>> True
Working on: #10000[ms] 10000 NF nan
Out:  10000.0 10000.0 ==>>> True
Working on: ENBEA1\STG400.QFC ENBEA1\STG400.QFC B1 nan
Out:  ENBEA1\STG400.QFC ENBEA1\STG400.QFC ==>>> True
Working on: ENBEA1\VPAR01.Q15 ENBEA1\VPAR01.Q15 B1 nan
Out:  ENBEA1\VPAR01.Q15 ENBEA1\VPAR01.Q15 ==>>> True
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: 1 1 B1 nan
Out:  True True ==>>> True
Working on: ENBEA1\STG400.E11 ENBEA1\STG400.E11 B1 nan
Out:  ENBEA1\STG400.E11 ENBEA1\STG400.E11 ==>>> True
Working on: ENBEA1\VPAR01.Q16 ENBEA1\VPAR01.Q16 B1 nan
Out:  ENBEA1\VPAR01.Q16 ENBEA1\VPAR01.Q16 ==>>> True
Working on: ENBEA1\VIHW12.Q5 ENBEA1\VIHW12.Q5 B1 nan
Out:  ENBEA1\VIHW12.Q5 ENBEA1\VIHW12.Q5 ==>>> True
Working on: ENBEA1\LS201.Q ENBEA1\LS201.Q B1 nan
Out:  ENBEA1\LS201.Q ENBEA1\LS201.Q ==>>> True
Working on: ENBEA1\AND_01.Q ENBEA1\AND_01.Q B1 nan
Out:  

signal type_base inout type_conv                              value  \
0           I        B1     <       NaN                                  1   
1           T        TF     <       NaN                              60[s]   
3          X1        N2     <        V2                                0H0   
4          X2        N2     <        V2                            $VIHW36   
5           I        B1     <       NaN                           ENMESS.Q   
7          X1        N2     <        V2                                0H0   
8          X2        N2     <        V2                            $VOHW01   
9           I        B1     <       NaN                           ENMESS.Q   
11         IS        V2     <       NaN                           NSW000.Y   
28         IS        V2     <       NaN                           NSW001.Y   
45         X1        N2     <        V2                                0H0   
46         X2        N2     <        V2                            $VISW01   
47          I        B1     <       NaN                           ENMESS.Q   
49         X1        N2     <        V2                                0H0   
50         X2        N2     <        V2                            $VOSW01   
51          I        B1     <       NaN                           ENMESS.Q   
53         IS        V2     <       NaN                           NSW002.Y   
70         IS        V2     <       NaN                           NSW003.Y   
87         X1        N2     <        O2                                036   
88         X2        N2     <        O2                                036   
89          I        B1     <       NaN                                  0   
91          X        N2     <        O2                              20006   
93        CMS        MR     -       NaN                             MESY_1   
94         T1        NS     -       NaN  '@C@85@ EN: Communication error '   
95         MT        B1     -       NaN                                  1   
96         RP        O2     <       NaN                            RPALL.Y   
97         RS        O2     <       NaN                            RSCOM.Y   
98         EN        B1     <       NaN                                  1   
99         I1        B1     <       NaN                                  0   
100        SM        B1     <       NaN                                  0   
...       ...       ...   ...       ...                                ...   
102018     I4        B1     <       NaN                                  0   
102020      I        B1     <       NaN                           STG633.Q   
102021      R        B1     <       NaN                                  0   
102022      T        TF     <       NaN                            500[ms]   
102024     X1        N2     <        V2                             0HFFFF   
102025     X2        N2     <        V2                             LB2.QS   
102026      I        B1     <       NaN                           STG672.Q   
102028    IS1        V2     <       NaN                           STG681.Y   
102029    IS2        V2     <       NaN                             0HFFFF   
102032     I1        B1     <       NaN                         STG400.E11   
102033     I2        B1     <       NaN                         STG400.E21   
102034     I3        B1     <       NaN                          VCC_12.Q2   
102035     I4        B1     <       NaN                           ON1022.Q   
102036     I5        B1     <       NaN                           ON1023.Q   
102037     I6        B1     <       NaN                            LS201.Q   
102038     I7        B1     <       NaN                            LS202.Q   
102039     I8        B1     <       NaN                                  0   
102040     I9        B1     <       NaN                                  0   
102041    I10        B1     <       NaN                                  0   
102042    I11        B1     <

In [19]:
#TEST SELECT FROM SIMADYND TABLE
data_s3[(data_s3['value']=="$VTGSS")]

signal type_base inout type_conv   value        cpu cpu_source  \
107028     QS        V2     >      None  $VTGSS  PN-D06_P3  PN-D06_P3   
112064     IS        V2     <      None  $VTGSS  PN-D06_P3  PN-D06_P3   

                cpu_link   chart   block      link      value_linked  
107028              None  AIN__3  ITGSIG        []            $VTGSS  
112064  PN-D06_P3_$VTGSS  AOUT_3  INPSIG  [$VTGSS]  AIN__3\ITGSIG.QS

In [66]:
#TEST SELECT FROM TDC TABLE
data_a1[(data_a1['block']=="DMD115")|(data_a1['block']=="DMD116")]

rack_cpu   chart   block signal value  \
36349  TX02\D04P04\  DIN__4  DMD115      X   NaN   
36350  TX02\D04P04\  DIN__4  DMD115      Y     0   
36351  TX02\D04P04\  DIN__4  DMD116      X   NaN   
36352  TX02\D04P04\  DIN__4  DMD116      Y     0   

                                   link  type    out  rack     cpu  \
36349                 DIN__4\DMD104.OUT  DINT  False  TX02  D04P04   
36350  "DCNTR4\DMDC05.X"DMODE4\DMDM05.X  DINT   True  TX02  D04P04   
36351                   DIN__4\DMD105.Q   INT  False  TX02  D04P04   
36352  "DMODE4\DMDM06.X"DCNTR4\DMDC06.X   INT   True  TX02  D04P04   

          chartblock chart_block_signal       value_linked  
36349  DIN__4/DMD115    DIN__4/DMD115.X  DIN__4\DMD104.OUT  
36350  DIN__4/DMD115    DIN__4/DMD115.Y    DCNTR4\DMDC05.X  
36351  DIN__4/DMD116    DIN__4/DMD116.X    DIN__4\DMD105.Q  
36352  DIN__4/DMD116    DIN__4/DMD116.Y    DMODE4\DMDM06.X

In [20]:

#report_comp_inputs(data_s3,data_a1,to_file = False)

In [21]:
#data_s3[data_s3['value']=="$BCSCDM"]